In [1]:
import urllib
import json
import pandas as pd
import numpy as np
import warnings
import pickle
from datetime import datetime
from datetime import timedelta
import statistics
warnings.filterwarnings('ignore')

In [2]:
#PICKLE_PATH = 'hopkins_conf_augmented0605.pkl'
PICKLE_PATH = 'hopkins_death_augmented0605.pkl'
#RESULT_PATH = 'hopkins.conf.0605.withgr.pkl'
RESULT_PATH = 'hopkins_death_withgr_augmented0605.pkl'


###### Open pickle file

In [3]:


hopkins_confirmed = pd.DataFrame()
 
hpcon_rates=pd.DataFrame()

with open(PICKLE_PATH, 'rb') as file:
    hopkins_confirmed = pickle.load(file)
    


hopkins_confirmed.insert(7,column='last relevant date',value=' ')

hopkins_confirmed.insert(7,column='first_7',value=np.nan)  # first 7 days after 5% inf croseed (if exist)
 
hopkins_confirmed.insert(7,column='EXP_GF_Q3',value=0.0 )     
hopkins_confirmed.insert(7,column='EXP_GF_Q2',value=0.0)  
hopkins_confirmed.insert(7,column='EXP_GF_Q1',value=0.0)   

hopkins_confirmed.insert(12,column='EXP_GF_ABOVE0',value=0.0 )
hopkins_confirmed.insert(12,column='EXP_GF_M01TO0',value=0.0 )
hopkins_confirmed.insert(13,column='EXP_GF_0TO01',value=0.0 )
hopkins_confirmed.insert(14,column='EXP_GF_01TO02',value=0.0 )
hopkins_confirmed.insert(15,column='EXP_GF_02TO03',value=0.0 )
hopkins_confirmed.insert(16,column='EXP_GF_03TO04',value=0.0 )
hopkins_confirmed.insert(17,column='EXP_GF_ABOVE04',value=0.0 )


print (hopkins_confirmed.columns)

print (hopkins_confirmed.columns[10:20])


hopkins_confirmed
    
        

#hpcon_datarows = pd.DataFrame()
#hpcon_datarows =hopkins_confirmed.index
    
#for row in hopkins_confirmed.iterrows():
#     hpcon_datarows.append(row)

#hpcon_datarows

Index(['Province_State', 'Country_Region', 'avg_m_tmp', 'avg_m_RH',
       'avg_m_precip', 'avg_m_wind', 'Max_Cases', 'EXP_GF_Q1', 'EXP_GF_Q2',
       'EXP_GF_Q3',
       ...
       '4/27/2020', '4/28/2020', '4/29/2020', '4/30/2020', '5/1/2020',
       '5/2/2020', '5/3/2020', '5/4/2020', '5/5/2020', '5/6/2020'],
      dtype='object', length=130)
Index(['first_7', 'last relevant date', 'EXP_GF_M01TO0', 'EXP_GF_0TO01',
       'EXP_GF_01TO02', 'EXP_GF_02TO03', 'EXP_GF_03TO04', 'EXP_GF_ABOVE04',
       'EXP_GF_ABOVE0', 'Max_Date'],
      dtype='object')


Province_State  \
coordinate                         information                                  
(-41.4545, 145.9707)               data                              Tasmania   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-40.9006, 174.886)                data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-38.4161, -63.6167)               data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-37.8136, 144.9631)               data                              Victoria   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-35.6751, -71.543)                data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-35.4735, 149.0124)               data          Australian Capital Territory   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
...                                                                       ...   
(60.472, 8.4689)                   data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(61.14998174, -149.14269860000005) data                                Alaska   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(63.0, 16.0)                       data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(64.0, 26.0)                       data                                   NaN   
                                   avg_d_RH                               NaN   
             

In [4]:
datarows = [row for row in hopkins_confirmed.iterrows()  if row[0][1]=='data']
#hopkins_confirmed.insert(7,column='last relevant date',value=np.nan)

 


### Obtain a list of dates (string of columns names which are dates , assumed to be a continouos sequence in the DF)


cur=0

for name in hopkins_confirmed.columns :
    if '2020' in name and '/' in name: # this is a date!
        datefound=True
        break
    cur +=1  
if datefound == False:
    print ('date not found in DF columns')
else:
    print ('first date is',name, 'offset',cur )
    firstdate=name
    firstdate_offset=cur 
    
rvrscur=len(hopkins_confirmed.columns)

for name in hopkins_confirmed.columns[::-1]:                #this loop will allow columns which are not dates right of dates
    if '2020' in name and '/' in name: # this is a date!
        break # this is  a date...
    else:
        rvrscur -=1
print ('rvrscur col',hopkins_confirmed.columns[rvrscur-1])
valid_dates=hopkins_confirmed.columns[cur:rvrscur]         # valid dates - all the dates in the index

print ('dates',valid_dates)
print ('last',valid_dates[-1])
 

for row in datarows:
    #print (row[0],row[0][1])
    ratios=[0]
    totals=[]
    deltas=[]
    last_tot=0
    actual_dates=[]
    
    for cursor in range (len(valid_dates)-1):
        p=row[1][valid_dates[cursor]]
        q=row[1][valid_dates[cursor+1]  ]
        actual_dates.append(valid_dates[cursor])
        
        
        
        if p > 0:
            ratios.append (round(q/p - 1,4 ))
            totals.append (p)
        else:
            if q>0:
                ratios.append (0)           # the first gr is set to 0  and will most often get removed due to
                                            # totals less then 5 pct,
            else: ratios.append(0)          #  0 growth between two zeros...
            totals.append(0)
            
    #ratios=[0]+ratios  # so that each growth rate 'sits' under its 'total' and is the growth between this and the 
                       # previous
    totals.append(row[1][valid_dates[-1]]) # add the last total to list
    actual_dates.append(valid_dates[-1])
   
    totals5=np.array(totals)
    
    mov_avg_5_totals= np.array([d/5 for d in totals5])
    ln=len(totals5)
    for j in range (1,5):
        mov_avg_5_totals[j:]=np.add(mov_avg_5_totals[j:], totals5[0:ln-j] /5 )
    
    deltas5=np.zeros_like(mov_avg_5_totals)
    for ind in range(1,len(deltas5)):
        deltas5[ind]=mov_avg_5_totals[ind]-mov_avg_5_totals[ind-1] 
    
    # calc the exponential growth (growth between this day mov_avg delta to prev. day mov_avg delta)
    mov_avg_5_ratio=np.zeros_like(deltas5)
    for ind in range (1,len(mov_avg_5_ratio)):
        if   deltas5[ind-1]==0 :  mov_avg_5_ratio[ind]=0
            
        else: mov_avg_5_ratio[ind]=   (deltas5[ind] / deltas5[ind-1]) - 1
            
    print ('==========')        
    print  ('new',row[1]['Province_State'],row[1][ 'Country_Region'])
    #print ('totals',totals)
    print ('totals5',totals5)
    print ('totals5 mov avg',mov_avg_5_totals)
    print ('deltas5',deltas5)
    print ('ratio5',mov_avg_5_ratio)
    e_ratios=mov_avg_5_ratio
       
    if max(totals)<20:
        print ('SKIP')
        continue    ###  if no day with 20 or more, skip this region,  small numbers 
    print ('NO SKIP')
        
   
    print (row[1]['Province_State'],row[1][ 'Country_Region'],ratios,totals)
    print ('lens',len(ratios),len(totals))
    maxt=max(totals)
    few=maxt/20
    print (row[1]['Province_State'],row[1][ 'Country_Region'],maxt,few)
    # here , find the 5% seperator
    few_seperator = -1
    first_confirmed_date   = None
    for cursor in range (len(totals)-1):
        
        if (first_confirmed_date == None) and totals[cursor] > 0 :   # foe exponential growth, we start from first positive
            first_confirmed_date=actual_dates[cursor]
            actual_exp_dates=actual_dates[cursor:]
            print ('exp cut, first confirmed, value, len before',first_confirmed_date,len(e_ratios))
            e_ratios=e_ratios[cursor:]
            e_sample=totals[cursor:]
            print ('exp cut, first confirmed, value, len after',first_confirmed_date,len(e_ratios))
          
            
        if  (totals[cursor] <=few ) and (totals [cursor+1]>=few):
            few_seperator=cursor
            break
    if few_seperator >=0 :
        t_sample=totals[cursor+1:]
        t_ratios=ratios[cursor+1:]
        actual_dates=actual_dates[cursor+1:]
        five_pct_name=actual_dates[0]
        
        print ('five pct', five_pct_name) 
    else:
        five_pct_name=actual_dates[0]  # this is the complete actual_dates
        print ('five pct not found',five_pct_name )
     # find the first positive confirmed date (for exponential date)
    
    #   find if there is a sequence of growth rate lower than 2% per day (from the end )  remove it if found
    
    for cur in range (len(t_ratios)):
        maxright=max(t_ratios[cur:])
        if   (maxright>0.02):
            continue
        else:
            print ('maxright ,cur, len ratios, rightside',maxright,cur,len(t_ratios),t_ratios[cur:],t_sample[cur:] )
            break
    
    
    last_relevant_sample=actual_dates[ -1]  # overriden if cut   
    if cur < len(t_ratios)-1:
     
        print ('cut right side len befor , len after',len(t_ratios),cur+1)
        
        t_ratios=t_ratios [:cur+1]
        t_sample=t_sample [:cur+1]
        actual_dates=actual_dates[:cur+1]
        last_relevant_sample=actual_dates[ -1]
        
        # here we cut also the exp relevant date, riding on previous calc of last relevant date
        print ('last date, e_ratio before',last_relevant_sample,e_ratios)
        for j in range(len(actual_exp_dates)):
            if actual_exp_dates[j]==last_relevant_sample: # cut the right side (same criteria as before, less than 2% )
                e_ratios=e_ratios[:j+1]
                e_sample=e_sample[:j+1]
                actual_exp_dates=actual_exp_dates[:j+1]
                break
        print ('last date, e_ratio after',last_relevant_sample,e_ratios)
            
            
        
    else: print ('nothing was cut')
            
    
    sorted_sample=t_sample.sort()
    
    
    print ('sample size',len(t_sample),t_sample,t_ratios)
    
    med=statistics.median(t_ratios)
    
    lower=np.percentile(t_ratios,25)
    upper=np.percentile(t_ratios,75)
    
    exp_med=round(statistics.median(e_ratios),4)
    
    exp_lower=round(np.percentile(e_ratios,25),4)
    exp_upper=round(np.percentile(e_ratios,75),4)
    print ('lower, median, upper, e..',lower,med,upper,exp_lower,exp_med,exp_upper)
    print ('e_ratios len, values',len(e_ratios),np.sort(e_ratios))
    
    npE=np.array(e_ratios)
    Epos=np.sum(npE > 0)
    EM01=((npE <= 0 ) & (npE>  -0.1)).sum()
    E1=((npE > 0 ) & (npE<= 0.1)).sum()
    E2=((npE > 0.1 ) & (npE<= 0.2)).sum()
    E3=((npE > 0.2 ) & (npE<= 0.3)).sum()
    E4=((npE > 0.3 ) & (npE<= 0.4)).sum()
    E5= (npE > 0.4 ).sum()
    
    print ('e POS m01 1 TO 5',EM01,Epos,E1,E2,E3,E4,E5)
    colslen=len(hopkins_confirmed)
    daycount=0
    sevendays=[]
    
    for smpl in t_sample:
        if smpl< few : continue
        else:
            daycount +=1
            if daycount==8 : break
            else: sevendays.append(smpl)
    if daycount==8:
        if sevendays[0]>0:
            
            seven_days_growth=(sevendays[-1]/sevendays[0])-1
    
        else:
            daycount=0
    else: daycount=0
     
    
    coord=row [0][0]
    if daycount>0:
        hopkins_confirmed.loc[coord, 'first_7']['data'] = seven_days_growth
        print ( 'Debug 7 ', seven_days_growth)
        
    hopkins_confirmed.loc[coord, '5%_Date']['data'] = five_pct_name
    hopkins_confirmed.loc[coord, 'last relevant date']['data']=last_relevant_sample
    hopkins_confirmed.loc[coord, 'GF_Q1']['data']=lower
    hopkins_confirmed.loc[coord, 'GF_Q2']['data']=med
    hopkins_confirmed.loc[coord, 'GF_Q3']['data']=upper
    hopkins_confirmed.loc[coord, 'EXP_GF_Q1']['data']=exp_lower
    hopkins_confirmed.loc[coord, 'EXP_GF_Q2']['data']=exp_med
    hopkins_confirmed.loc[coord, 'EXP_GF_Q3']['data']=exp_upper
    hopkins_confirmed.loc[coord, 'EXP_GF_ABOVE0']['data']=Epos
    
    #print ('Debug 0 ',hopkins_confirmed.loc[coord,'EXP_GF_Q1']['data'], 
     #      hopkins_confirmed.loc[coord,'EXP_GF_Q3']['data'])
  
    hopkins_confirmed.loc[coord,'EXP_GF_M01TO0']['data']=EM01 
    hopkins_confirmed.loc[coord,'EXP_GF_0TO01']['data']=E1 
    hopkins_confirmed.loc[coord,'EXP_GF_01TO02']['data']=E2
    hopkins_confirmed.loc[coord,'EXP_GF_02TO03']['data']=E3
    hopkins_confirmed.loc[coord,'EXP_GF_03TO04']['data']=E4
    hopkins_confirmed.loc[coord,'EXP_GF_ABOVE04']['data']=E5 
    #hopkins_confirmed.loc[(row[0][0],'Growth rates'),:]=   (  pd.Series([np.nan]*colslen) )     # add the row
    #print  ('row added ',row[0][0],row[0][1])
    
    #xx=hopkins_confirmed.loc[(row[0][0])].loc['data'].at['5%_Date'] 
        
    #hopkins_confirmed.loc[(row[0][0])].loc['data'].at['5%_Date'] =five_pct_name
    #xx2=hopkins_confirmed.loc[(row[0][0])].loc['data'].at['5%_Date'] 
    
    #print ('xx, xx2,xx3',xx,xx2 ) 
    #print ('last',last_relevant_sample)
    ##hopkins_confirmed.at[(row[0][0],'Growth rates'),'last relevant date']=last_relevant_sample
    #hopkins_confirmed.at[(row[0][0],'Growth rates'),'GF_Q1']=lower
    #hopkins_confirmed.at[(row[0][0],'Growth rates'),'GF_Q2']=med
    #hopkins_confirmed.at[(row[0][0],'Growth rates'),'GF_Q3']=upper
    #for cursor in range(len(actual_dates)):
    #    date=actual_dates[cursor]
    #    hopkins_confirmed.at[(row[0][0],'Growth rates'),date]=t_ratios[cursor]
    
    print ('DEBUG1' , row[1]['Province_State'],row[1][ 'Country_Region'],maxt,few)
    print ('DEBUG2' , lower, med, upper,five_pct_name,len(actual_dates),len(t_ratios))
    print ('DEBUG2E' , exp_lower, exp_med, exp_upper, len(actual_exp_dates),len(e_ratios))
    print ('DEBUG3', e_ratios)
    print ('DEBUG4', e_sample)
    print ('DEBUG5',hopkins_confirmed.loc[(row[0][0])])
    
    
      
        
hopkins_confirmed 
                 
 

first date is 1/22/2020 offset 24
rvrscur col 5/6/2020
dates Index(['1/22/2020', '1/23/2020', '1/24/2020', '1/25/2020', '1/26/2020',
       '1/27/2020', '1/28/2020', '1/29/2020', '1/30/2020', '1/31/2020',
       ...
       '4/27/2020', '4/28/2020', '4/29/2020', '4/30/2020', '5/1/2020',
       '5/2/2020', '5/3/2020', '5/4/2020', '5/5/2020', '5/6/2020'],
      dtype='object', length=106)
last 5/6/2020
new Tasmania Australia
totals5 [ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  1.  2.  2.
  2.  2.  2.  2.  2.  3.  3.  4.  4.  5.  5.  6.  6.  6.  7.  7.  7.  7.
  7.  7.  8.  9. 10. 11. 11. 11. 12. 13. 13. 13. 13. 13. 13. 13.]
totals5 mov avg [ 0.   0.   0.   0.   0.   0.   0.   0.   0.   0.   0.   0.   0.   0.
  0.   0.   0.   0.   0.   0.   0.   0.   0.   0.

DEBUG1 nan New Zealand 21.0 1.05
DEBUG2 0.0 0.0 0.0871 4/10/2020 27 27
DEBUG2E -0.0625 0.0 0.0 39 39
DEBUG3 [ 0.00000000e+00  0.00000000e+00  2.22044605e-16 -5.55111512e-16
  0.00000000e+00 -1.00000000e+00  0.00000000e+00  0.00000000e+00
  0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
  0.00000000e+00  2.00000000e+00  4.44089210e-16  3.33333333e-01
  1.00000000e+00 -1.25000000e-01 -2.85714286e-01  4.00000000e-01
 -1.42857143e-01 -5.00000000e-01  0.00000000e+00  3.33333333e-01
 -2.50000000e-01  1.00000000e+00  2.88657986e-15 -2.99760217e-15
  2.88657986e-15 -1.66666667e-01 -6.00000000e-01 -5.00000000e-01
 -1.77635684e-14  0.00000000e+00  1.77635684e-14 -1.77635684e-14
  0.00000000e+00  1.00000000e+00 -5.00000000e-01]
DEBUG4 [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 4.0, 4.0, 5.0, 9.0, 9.0, 9.0, 11.0, 11.0, 12.0, 12.0, 13.0, 14.0, 17.0, 18.0, 18.0, 19.0, 19.0, 19.0, 19.0, 19.0, 20.0, 20.0, 20.0, 20.0, 21.0, 21.0]
DEBUG5              Province_State

DEBUG1 nan Argentina 273.0 13.65
DEBUG2 0.034075 0.05445 0.088875 3/28/2020 40 40
DEBUG2E -0.029 0.0 0.1772 60 60
DEBUG3 [ 0.00000000e+00  0.00000000e+00  2.22044605e-16 -5.55111512e-16
  0.00000000e+00  0.00000000e+00  0.00000000e+00  1.11022302e-15
 -1.11022302e-15  0.00000000e+00 -1.00000000e+00  0.00000000e+00
  2.22044605e-15  1.00000000e+00  1.11022302e-15  0.00000000e+00
  5.00000000e-01  6.66666667e-01  8.88178420e-16  8.00000000e-01
  5.55555556e-01 -7.14285714e-02  1.53846154e-01  2.00000000e-01
 -1.66666667e-01  2.00000000e-01  1.11111111e-01 -8.88178420e-16
 -1.50000000e-01  1.76470588e-01 -1.77635684e-15  2.00000000e-01
  2.08333333e-01  3.10344828e-01 -7.89473684e-02 -2.85714286e-02
  1.99840144e-15 -1.17647059e-01 -3.33333333e-02  1.03448276e-01
  3.12500000e-02 -3.03030303e-02 -6.25000000e-02 -1.66666667e-01
  2.80000000e-01 -9.37500000e-02  2.41379310e-01  2.22222222e-01
  1.13636364e-01 -8.16326531e-02 -6.32827124e-15 -6.66666667e-02
 -9.52380952e-02 -1.31578947e-01 -

DEBUG1 nan Chile 281.0 14.05
DEBUG2 0.044024999999999995 0.0566 0.122275 4/1/2020 36 36
DEBUG2E -0.0 0.0367 0.1569 46 46
DEBUG3 [ 0.00000000e+00  1.00000000e+00 -4.44089210e-16  5.00000000e-01
  3.33333333e-01 -2.22044605e-16  6.66133815e-16  2.50000000e-01
  1.77635684e-15  6.00000000e-01  3.75000000e-01  9.09090909e-02
  2.50000000e-01  2.66666667e-01  1.57894737e-01 -4.54545455e-02
  1.90476190e-01  4.00000000e-02  1.53846154e-01  3.33333333e-02
  1.61290323e-01  2.77777778e-02 -8.10810811e-02  2.94117647e-02
 -1.71428571e-01  1.03448276e-01  1.25000000e-01  2.22222222e-01
 -6.81818182e-02  9.75609756e-02 -6.66666667e-02  4.76190476e-02
 -4.54545455e-02 -2.38095238e-02  2.43902439e-02  3.33066907e-15
 -9.52380952e-02  2.63157895e-02  7.69230769e-02  9.52380952e-02
 -2.17391304e-02  8.88888889e-02  8.16326531e-02  1.88679245e-02
 -1.11111111e-01 -2.08333333e-02]
DEBUG4 [1.0, 2.0, 2.0, 3.0, 4.0, 5.0, 6.0, 7.0, 8.0, 12.0, 16.0, 18.0, 22.0, 27.0, 34.0, 37.0, 43.0, 48.0, 57.0, 65.0, 73.0

DEBUG1 New South Wales Australia 44.0 2.2
DEBUG2 0.0 0.0 0.0878 3/17/2020 51 51
DEBUG2E -0.125 0.0 0.0 64 64
DEBUG3 [ 0.00000000e+00  0.00000000e+00  2.22044605e-16 -5.55111512e-16
  1.00000000e+00 -5.00000000e-01  1.11022302e-15 -1.11022302e-15
  0.00000000e+00 -1.00000000e+00  0.00000000e+00  0.00000000e+00
  0.00000000e+00  0.00000000e+00  5.00000000e-01 -7.77156117e-16
  3.33333333e-01 -1.11022302e-15 -5.00000000e-01 -5.00000000e-01
  1.00000000e+00 -5.00000000e-01 -4.44089210e-15  4.44089210e-15
  1.00000000e+00 -5.00000000e-01  8.88178420e-15 -8.88178420e-15
  1.00000000e+00  4.44089210e-15  1.00000000e+00 -2.22044605e-15
  1.00000000e+00  1.25000000e-01  2.22222222e-01 -1.81818182e-01
  3.99680289e-15 -3.33333333e-01 -1.66666667e-01 -4.00000000e-01
  3.33333333e-01 -4.44089210e-15 -2.50000000e-01 -3.33333333e-01
 -8.88178420e-15 -5.00000000e-01  1.77635684e-14 -1.77635684e-14
  0.00000000e+00 -1.00000000e+00  0.00000000e+00  4.00000000e-01
  0.00000000e+00  1.42857143e-01  0.000

...

DEBUG1 nan Russia 1537.0 76.85
DEBUG2 0.0857 0.1211 0.14755000000000001 4/10/2020 27 27
DEBUG2E 0.0 0.0765 0.1576 49 49
DEBUG3 [ 0.00000000e+00  0.00000000e+00  2.22044605e-16 -5.55111512e-16
  0.00000000e+00 -1.00000000e+00  0.00000000e+00  0.00000000e+00
  5.00000000e-01 -7.77156117e-16  1.33333333e+00 -1.42857143e-01
  1.33333333e+00  4.28571429e-01  3.00000000e-01 -3.33066907e-16
  3.07692308e-01 -1.76470588e-01 -1.78571429e-01  2.17391304e-01
  3.57142857e-02  1.37931034e-01  4.84848485e-01  2.04081633e-01
  2.20338983e-01  1.80555556e-01  1.05882353e-01  1.06382979e-01
  2.11538462e-01  1.34920635e-01  1.53846154e-01  1.57575758e-01
  8.37696335e-02  8.21256039e-02  7.14285714e-02  8.33333333e-03
  4.95867769e-02  8.66141732e-02  5.43478261e-02 -3.43642612e-02
  1.10320285e-01  1.44230769e-01  9.80392157e-02  7.65306122e-02
  1.42180095e-02 -3.50467290e-02 -7.02179177e-02 -1.56250000e-02
 -2.64550265e-02]
DEBUG4 [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 3.0, 3.0, 4.0, 4.0, 8.0, 9.0, 17.0, 2

DEBUG1 nan Norway 216.0 10.8
DEBUG2 0.0373 0.0704 0.1452 3/24/2020 33 33
DEBUG2E -0.0464 0.0 0.1436 43 43
DEBUG3 [ 0.00000000e+00  0.00000000e+00 -2.22044605e-16  4.44089210e-16
  1.00000000e+00 -3.33333333e-01  6.66133815e-16  0.00000000e+00
  1.11022302e-15 -1.11022302e-15  2.50000000e-01  4.00000000e-01
  1.33226763e-15  7.14285714e-01  8.33333333e-02  6.66133815e-16
  3.84615385e-01  3.88888889e-01  1.33226763e-15  8.00000000e-02
  2.59259259e-01 -1.17647059e-01  6.66666667e-02 -2.22044605e-15
  2.18750000e-01  7.69230769e-02  9.52380952e-02 -8.69565217e-02
  2.38095238e-02 -9.30232558e-02 -1.53846154e-01 -6.06060606e-02
  1.93548387e-01 -1.08108108e-01  0.00000000e+00 -9.09090909e-02
 -1.33333333e-01  1.92307692e-01 -3.22580645e-02 -1.33333333e-01
  1.53846154e-01  1.33333333e-01 -4.11764706e-01]
DEBUG4 [3.0, 3.0, 3.0, 3.0, 6.0, 7.0, 7.0, 7.0, 7.0, 10.0, 12.0, 14.0, 14.0, 19.0, 23.0, 25.0, 32.0, 39.0, 44.0, 50.0, 59.0, 62.0, 71.0, 76.0, 89.0, 101.0, 108.0, 113.0, 119.0, 128.0, 134

DEBUG1 nan Sweden 2941.0 147.05
DEBUG2 0.026 0.0503 0.124 3/31/2020 37 37
DEBUG2E -0.0503 0.0769 0.2431 57 57
DEBUG3 [ 0.00000000e+00  0.00000000e+00  2.22044605e-16  1.00000000e+00
  5.00000000e-01  6.66666667e-01  2.00000000e-01  5.00000000e-01
  0.00000000e+00  4.44444444e-01  7.69230769e-02 -1.22124533e-15
  7.14285714e-02  6.66666667e-01  8.40000000e-01  2.39130435e-01
  4.73684211e-01 -4.76190476e-02 -7.50000000e-02  1.35135135e-01
  2.26190476e-01  3.00970874e-01  5.14925373e-01  2.21674877e-01
 -8.46774194e-02 -2.64317181e-02  7.69230769e-02  1.89075630e-01
  1.62544170e-01  2.76595745e-01  1.16666667e-01 -1.25799574e-01
 -2.48780488e-01 -2.46753247e-01  3.44827586e-02  3.87500000e-01
  3.39339339e-01  1.23318386e-01  1.81636727e-01 -1.43581081e-01
 -2.56410256e-01  1.45888594e-01  2.43055556e-01 -5.02793296e-02
  2.00000000e-01  0.00000000e+00 -2.99019608e-01 -2.14452214e-01
 -8.90207715e-03 -7.18562874e-02  2.70967742e-01  1.64974619e-01
 -1.39433551e-01 -1.79746835e-01 -5.24

DEBUG1 nan Finland 252.0 12.6
DEBUG2 0.0296 0.0504 0.12375 3/30/2020 38 38
DEBUG2E -0.034 0.0152 0.1844 47 47
DEBUG3 [ 0.00000000e+00  0.00000000e+00  2.22044605e-16 -5.55111512e-16
  2.00000000e+00  3.33333333e-01  5.00000000e-01  3.33333333e-01
  2.50000000e-01  0.00000000e+00  2.00000000e-01 -1.66666667e-01
 -2.66453526e-15 -1.00000000e-01  3.33333333e-01 -8.33333333e-02
 -9.09090909e-02  5.00000000e-01  3.33333333e-01 -1.50000000e-01
  1.76470588e-01  1.00000000e-01  1.55431223e-15 -1.36363636e-01
  1.57894737e-01  9.09090909e-02  8.33333333e-02 -2.77555756e-15
  1.92307692e-01 -3.22580645e-02 -1.33333333e-01  1.53846154e+00
  1.51515152e-02  2.23880597e-01  1.21951220e-02  6.02409639e-02
 -4.43181818e-01 -1.02040816e-01 -3.86363636e-01  7.40740741e-02
 -1.37931034e-01  1.20000000e-01 -3.57142857e-02  1.48148148e-01
  9.67741935e-02  2.94117647e-02 -2.85714286e-02]
DEBUG4 [1.0, 1.0, 1.0, 1.0, 3.0, 5.0, 7.0, 9.0, 11.0, 13.0, 17.0, 17.0, 19.0, 20.0, 25.0, 28.0, 27.0, 34.0, 40.0, 42.0

Province_State  \
coordinate                         information                                  
(-41.4545, 145.9707)               data                              Tasmania   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-40.9006, 174.886)                data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-38.4161, -63.6167)               data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-37.8136, 144.9631)               data                              Victoria   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-35.6751, -71.543)                data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-35.4735, 149.0124)               data          Australian Capital Territory   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
...                                                                       ...   
(60.472, 8.4689)                   data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(61.14998174, -149.14269860000005) data                                Alaska   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(63.0, 16.0)                       data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(64.0, 26.0)                       data                                   NaN   
                                   avg_d_RH                               NaN   
             

In [5]:
look=hopkins_confirmed[[ 'Province_State',  'Country_Region','first_7']]
for row in look.iterrows() :
    if row[0][1]=='data' : 
         print (row[1][0:3])

Province_State     Tasmania
Country_Region    Australia
first_7                 NaN
Name: ((-41.4545, 145.9707), data), dtype: object
Province_State            NaN
Country_Region    New Zealand
first_7                   3.5
Name: ((-40.9006, 174.886), data), dtype: object
Province_State          NaN
Country_Region    Argentina
first_7             1.16667
Name: ((-38.4161, -63.6167), data), dtype: object
Province_State     Victoria
Country_Region    Australia
first_7                 NaN
Name: ((-37.8136, 144.9631), data), dtype: object
Province_State       NaN
Country_Region     Chile
first_7           1.6875
Name: ((-35.6751, -71.543), data), dtype: object
Province_State    Australian Capital Territory
Country_Region                       Australia
first_7                                    NaN
Name: ((-35.4735, 149.0124), data), dtype: object
Province_State    South Australia
Country_Region          Australia
first_7                       NaN
Name: ((-34.9285, 138.6007), data), dtype:

Name: ((30.83568832, -83.27056716), data), dtype: object
Province_State    Georgia
Country_Region         US
first_7               NaN
Name: ((30.83922642, -83.58303423), data), dtype: object
Province_State    Louisiana
Country_Region           US
first_7                 NaN
Name: ((30.84425359, -91.04976723), data), dtype: object
Province_State    Louisiana
Country_Region           US
first_7                   0
Name: ((30.85288548, -90.03866652), data), dtype: object
Province_State    Georgia
Country_Region         US
first_7               1.5
Name: ((30.86392347, -83.91847289), data), dtype: object
Province_State    Georgia
Country_Region         US
first_7               NaN
Name: ((30.87454847, -84.23418364), data), dtype: object
Province_State    Louisiana
Country_Region           US
first_7                 NaN
Name: ((30.87882871, -91.4148538), data), dtype: object
Province_State    Georgia
Country_Region         US
first_7               NaN
Name: ((30.87967778, -84.57619536), da

Name: ((33.79696941, -90.87372121), data), dtype: object
Province_State    Georgia
Country_Region         US
first_7               NaN
Name: ((33.83749973, -83.43679568), data), dtype: object
Province_State        NaN
Country_Region    Lebanon
first_7                 0
Name: ((33.8547, 35.8623), data), dtype: object
Province_State    Georgia
Country_Region         US
first_7               NaN
Name: ((33.878629600000004, -83.08278123), data), dtype: object
Province_State    Henan
Country_Region    China
first_7               0
Name: ((33.882, 113.614), data), dtype: object
Province_State    Mississippi
Country_Region             US
first_7                     0
Name: ((33.89236763, -88.4808438), data), dtype: object
Province_State    South Carolina
Country_Region                US
first_7                      NaN
Name: ((33.89665987, -81.27146426), data), dtype: object
Province_State    South Carolina
Country_Region                US
first_7                      NaN
Name: ((33.91826534,

Name: ((36.89934014, -76.26420872), data), dtype: object
Province_State    Virginia
Country_Region          US
first_7                NaN
Name: ((36.90579348, -76.70842863), data), dtype: object
Province_State    Virginia
Country_Region          US
first_7                NaN
Name: ((37.03513786, -76.35879121), data), dtype: object
Province_State    Kentucky
Country_Region          US
first_7                NaN
Name: ((37.05350953, -88.70445755), data), dtype: object
Province_State    California
Country_Region            US
first_7                  NaN
Name: ((37.05580291, -122.0066524), data), dtype: object
Province_State    Missouri
Country_Region          US
first_7                NaN
Name: ((37.05588075, -89.56474493), data), dtype: object
Province_State    Virginia
Country_Region          US
first_7                NaN
Name: ((37.08166899, -76.51754109), data), dtype: object
Province_State        NaN
Country_Region         US
first_7           1.95205
Name: ((37.0902, -95.7129), dat

Name: ((39.52305623, -85.79158570000001), data), dtype: object
Province_State    Illinois
Country_Region          US
first_7                NaN
Name: ((39.54581621, -89.27780482), data), dtype: object
Province_State    Hebei
Country_Region    China
first_7             NaN
Name: ((39.549, 116.1306), data), dtype: object
Province_State    Maryland
Country_Region          US
first_7                0.8
Name: ((39.55010644, -76.30775940000002), data), dtype: object
Province_State    Maryland
Country_Region          US
first_7                3.5
Name: ((39.56453592, -77.02373735), data), dtype: object
Province_State    Maryland
Country_Region          US
first_7                NaN
Name: ((39.56647682, -75.94627411), data), dtype: object
Province_State    Delaware
Country_Region          US
first_7                0.8
Name: ((39.57992638, -75.64054974), data), dtype: object
Province_State    Colorado
Country_Region          US
first_7                0.8
Name: ((39.58635604, -105.2517692), data

Name: ((41.78869215, -76.51570822), data), dtype: object
Province_State    Massachusetts
Country_Region               US
first_7                  1.6875
Name: ((41.79228404, -71.10872211), data), dtype: object
Province_State    Connecticut
Country_Region             US
first_7                   2.2
Name: ((41.7937534, -73.2451475), data), dtype: object
Province_State    Connecticut
Country_Region             US
first_7               1.77083
Name: ((41.80283011, -72.73103891), data), dtype: object
Province_State    Pennsylvania
Country_Region              US
first_7                    NaN
Name: ((41.82147784, -75.80071959), data), dtype: object
Province_State    Connecticut
Country_Region             US
first_7                   NaN
Name: ((41.82972709, -71.98182316), data), dtype: object
Province_State    Illinois
Country_Region          US
first_7             1.8972
Name: ((41.84144849, -87.81658794), data), dtype: object
Province_State    Illinois
Country_Region          US
first_7  

Name: ((51.2538, -85.3232), data), dtype: object
Province_State       NaN
Country_Region    Poland
first_7                2
Name: ((51.9194, 19.1451), data), dtype: object
Province_State            NaN
Country_Region    Netherlands
first_7               2.13043
Name: ((52.1326, 5.2913), data), dtype: object
Province_State    Saskatchewan
Country_Region          Canada
first_7                    NaN
Name: ((52.9399, -106.4509), data), dtype: object
Province_State    Quebec
Country_Region    Canada
first_7              1.4
Name: ((52.9399, -73.5491), data), dtype: object
Province_State    Newfoundland and Labrador
Country_Region                       Canada
first_7                                 NaN
Name: ((53.1355, -57.6604), data), dtype: object
Province_State        NaN
Country_Region    Ireland
first_7            1.4507
Name: ((53.1424, -7.6921), data), dtype: object
Province_State        NaN
Country_Region    Belarus
first_7             1.875
Name: ((53.7098, 27.9534), data), dtype

In [8]:
hopkins_confirmed.to_csv('hopdeath56.csv')

###### Calculate growth factors

In [6]:
hopkins_confirmed 
#hopkins_confirmed.columns



#dataonly=hopkins_confirmed['information']=='data'
#hopconf_data=hopkins_confirmed[dataonly]
#hopconf_data

Province_State  \
coordinate                         information                                  
(-41.4545, 145.9707)               data                              Tasmania   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-40.9006, 174.886)                data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-38.4161, -63.6167)               data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-37.8136, 144.9631)               data                              Victoria   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-35.6751, -71.543)                data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(-35.4735, 149.0124)               data          Australian Capital Territory   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
...                                                                       ...   
(60.472, 8.4689)                   data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(61.14998174, -149.14269860000005) data                                Alaska   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(63.0, 16.0)                       data                                   NaN   
                                   avg_d_RH                               NaN   
                                   avg_d_precip                           NaN   
                                   avg_d_tmp                              NaN   
                                   avg_d_wind                             NaN   
(64.0, 26.0)                       data                                   NaN   
                                   avg_d_RH                               NaN   
             

###### Save file as pickle

In [9]:
pickle_path = RESULT_PATH.format(datetime.now().strftime('%d%m'))
with open(pickle_path, 'wb') as file:
    pickle.dump(hopkins_confirmed, file)